In [2]:
import pandas as pd
import polars as pl
import datetime as dt
pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)
import numpy as np

In [3]:
import sys

sys.path.append("..")
from tooling.enums import AssetClass, Index, Spot, StrikeSpread
from tooling.fetch import fetch_option_data, fetch_spot_data
from tooling.filter import find_atm, option_tool

from fetching_from_local_db.enums import AssetClass, Index, StrikeSpread
from fetching_from_local_db.fetch_from_db import _fetch_batch, fetch_data, fetch_spot_data

In [4]:
tb = pd.read_csv('lobster_fixed.csv')
# tb = tb.drop(columns=['Unnamed: 0'])

In [5]:
tb

Day      Time  Strike      Expiry  DTE Option Type  Entry Price  \
0     2019-01-01  09:15:00   11000  2019-01-03    2          CE          NaN   
1     2019-01-01  09:15:00   10750  2019-01-03    2          PE          NaN   
2     2019-01-02  09:15:00   11000  2019-01-03    1          CE          NaN   
3     2019-01-02  09:15:00   10750  2019-01-03    1          PE          NaN   
4     2019-01-03  09:15:00   10900  2019-01-03    0          CE          NaN   
5     2019-01-03  09:15:00   10700  2019-01-03    0          PE          NaN   
6     2019-01-04  09:15:00   10800  2019-01-10    6          CE          NaN   
7     2019-01-04  09:15:00   10600  2019-01-10    6          PE          NaN   
8     2019-01-07  09:15:00   10900  2019-01-10    3          CE          NaN   
9     2019-01-07  09:15:00   10700  2019-01-10    3          PE          NaN   
10    2019-01-08  09:15:00   10900  2019-01-10    2          CE          NaN   
11    2019-01-08  09:15:00   10700  2019-01-10    2          PE          NaN   
12    2019-01-09  09:15:00   10950  2019-01-10    1          CE          NaN   
13    2019-01-09  09:15:00   10750  2019-01-10    1          PE          NaN   
14    2019-01-10  09:15:00   10950  2019-01-10    0          CE          NaN   
15    2019-01-10  09:15:00   10750  2019-01-10    0          PE          NaN   
16    2019-01-11  09:15:00   10950  2019-01-17    6          CE          NaN   
17    2019-01-11  09:15:00   10750  2019-01-17    6          PE          NaN   
18    2019-01-14  09:15:00   10900  2019-01-17    3          CE          NaN   
19    2019-01-14  09:15:00   10700  2019-01-17    3          PE          NaN   
20    2019-01-15  09:15:00   10900  2019-01-17    2          CE          NaN   
21    2019-01-15  09:15:00   10650  2019-01-17    2          PE          NaN   
22    2019-01-16  09:15:00   11000  2019-01-17    1          CE          NaN   
23    2019-01-16  09:15:00   10800  2019-01-17    1          PE          NaN   
24    2019-01-17  09:15:00   11050  2019-01-17    0          CE          NaN   
25    2019-01-17  09:15:00   10800  2019-01-17    0          PE          NaN   
26    2019-01-18  09:15:00   11000  2019-01-24    6          CE          NaN   
27    2019-01-18  09:15:00   10800  2019-01-24    6          PE          NaN   
28    2019-01-21  09:15:00   11050  2019-01-24    3          CE          NaN   
29    2019-01-21  09:15:00   10800  2019-01-24    3          PE          NaN   
30    2019-01-22  09:15:00   11050  2019-01-24    2          CE          NaN   
31    2019-01-22  09:15:00   10850  2019-01-24    2          PE          NaN   
32    2019-01-23  09:15:00   11050  2019-01-24    1          CE          NaN   
33    2019-01-23  09:15:00   10800  2019-01-24    1          PE          NaN   
34    2019-01-24  09:15:00   10950  2019-01-24    0          CE          NaN   
35    2019-01-24  09:15:00   10750  2019-01-24    0          PE          NaN   
36    2019-01-25  09:15:00   10950  2019-01-31    6          CE        66.45   
37    2019-01-25  09:15:00   10750  2019-01-31    6          PE        25.30   
38    2019-01-28  09:15:00   10900  2019-01-31    3          CE        32.40   
39    2019-01-28  09:15:00   10700  2019-01-31    3          PE        50.00   
40    2019-01-29  09:15:00   10750  2019-01-31    2          CE        31.30   
41    2019-01-29  09:15:00   10550  2019-01-31    2          PE        38.20   
42    2019-01-30  09:15:00   10800  2019-01-31    1          CE        16.65   
43    2019-01-30  09:15:00   10600  2019-01-31    1          PE        16.05   
44    2019-01-31  09:15:00   10800  2019-01-31    0          CE         2.60   
45    2019-01-31  09:15:00   10600  2019-01-31    0          PE         3.80   
46    2019-02-01  09:15:00   10950  2019-02-07    6          CE          NaN   
47    2019-02-01  09:15:00   10750  2019-02-07    6          PE          NaN   
48    2019-02-04  09:15:00   11000  2019-02-07    3          CE          NaN   
49    2019-02

In [6]:
tb['ROI%'].sum()

485.02517979874494

In [7]:
# def round_to_nearest_50(value):
#     return int(50 * round(value / 50))

# def get_hedge_pct(margin):
#     if 100 < margin <= 150:
#         return 5
#     elif 150 < margin <= 200:
#         return 4
#     elif 200 < margin < 300:
#         return 3
#     else:
#         return 0  # Default value if margin doesn't fit any range

# async def add_hedges(df):
#     # df.drop(columns=['ROI%', 'Trade Year'], inplace=True)
#     # hedge_pct = 2.75
#     index_name = "NIFTY"
#     index_str_for_opt = "nifty"

#     df["Hedge Strike"] = df.apply(
#         lambda row: (
#             int(round_to_nearest_50(row["strike"] * (1 + (get_hedge_pct(row["Margin"]) / 100))))
#             if row["type"] == "C" and row["Margin"] > 100
#             else int(round_to_nearest_50(row["strike"] * (1 - (get_hedge_pct(row["Margin"]) / 100))))
#             if row["type"] == "P" and row["Margin"] > 100
#             else 0  # Default value if neither condition matches
#         ),
#         axis=1,
#     )

#     # df["Hedge Contract"] = df.apply(
#     #     lambda row: get_option_contract_name2(
#     #         index_name, row["Hedge Strike"], row["Expiry"], row["Option Type"]
#     #     ),
#     #     axis=1,
#     # )

#     df["Hedge Entry Price"] = np.nan
#     df["Hedge Exit Price"] = np.nan

#     # print(df['Hedge Strike'].to_string())

#     for i in range(0, len(df)):
#         print(df.iloc[i]['date'])
#         if df.iloc[i]['Hedge Strike']:
#             # print(df.iloc[i]["Week"])
#             entry_date = df.iloc[i]['date']
#             entry_time = df.iloc[i]['Entry Time']
#             exit_date = df.iloc[i]['Exit date']
#             exit_time = df.iloc[i]['Exit Time']
#             hedge_strike = int(df.iloc[i]["Hedge Strike"])
#             hedge_expiry = df.iloc[i]["expiry"]
#             hedge_opt_type = df.iloc[i]["type"]
#             # hedge_entry_datetime = dt.datetime.combine(entry_date, entry_time)
#             # hedge_exit_datetime = dt.datetime.combine(exit_date, exit_time)
    
#             hedge_df = await fetch_data(
#                 index=index_str_for_opt,
#                 start_date=dt.datetime.strptime(entry_date, "%Y-%m-%d").date(),
#                 end_date=dt.datetime.strptime(exit_date, "%Y-%m-%d").date(),
#                 start_time=dt.datetime.strptime(entry_time, "%H:%M:%S").time(),
#                 end_time=dt.datetime.strptime(exit_time, "%H:%M:%S").time(),
#                 expiry=dt.datetime.strptime(hedge_expiry, "%Y-%m-%d"),
#                 strike=hedge_strike,
#                 asset_class=hedge_opt_type,
#             )
#             if not isinstance(hedge_df, str) and hedge_df is not None:
#                 hedge_df = hedge_df.to_pandas()
#             else:
#                 print(hedge_df)
#                 df.loc[i, "Hedge Entry Price"] = 0
#                 df.loc[i, "Hedge Exit Price"] = 0
#                 continue
#             # print(hedge_df)
    
#             hedge_entry_price = hedge_df.iloc[0]["c"]
#             hedge_exit_price = hedge_df.iloc[-1]["c"]
    
#             print(hedge_entry_price, hedge_exit_price)
    
#             df.loc[i, "Hedge Entry Price"] = hedge_entry_price
#             df.loc[i, "Hedge Exit Price"] = hedge_exit_price
    
#     return df

In [8]:
def round_to_nearest_50(value):
    return int(50 * round(value / 50))

def get_hedge_pct(margin):
    if 100 < margin <= 150:
        return 4
    elif 150 < margin <= 200:
        return 3
    elif 200 < margin <= 300:
        return 2
    else:
        return 0  # Default value if margin doesn't fit any range

async def add_hedges(df):
    # df.drop(columns=['ROI%', 'Trade Year'], inplace=True)
    # hedge_pct = 2.75
    index_name = "NIFTY"
    index_str_for_opt = "nifty"

    df["Hedge Strike"] = df.apply(
        lambda row: (
            int(round_to_nearest_50(row["Strike"] * (1 + (get_hedge_pct(row["Margin"]) / 100))))
            if row["Option Type"] == "CE" and row["Margin"] > 100
            else int(round_to_nearest_50(row["Strike"] * (1 - (get_hedge_pct(row["Margin"]) / 100))))
            if row["Option Type"] == "PE" and row["Margin"] > 100
            else 0  # Default value if neither condition matches
        ),
        axis=1,
    )

    # df["Hedge Contract"] = df.apply(
    #     lambda row: get_option_contract_name2(
    #         index_name, row["Hedge Strike"], row["Expiry"], row["Option Type"]
    #     ),
    #     axis=1,
    # )

    df["Hedge Entry Price"] = np.nan
    df["Hedge Exit Price"] = np.nan

    # print(df['Hedge Strike'].to_string())

    df['Entry Time'] = df['Time']

    for i in range(0, len(df)):
        print(df.iloc[i]['Day'])
        if df.iloc[i]['Hedge Strike']:
            # print(df.iloc[i]["Week"])
            entry_date = df.iloc[i]['Day']
            entry_time = df.iloc[i]['Entry Time']
            exit_date = df.iloc[i]['Day']
            exit_time = pd.to_datetime(df.iloc[i]['Exit Time']).time()
            hedge_strike = int(df.iloc[i]["Hedge Strike"])
            hedge_expiry = df.iloc[i]["Expiry"]
            hedge_opt_type = df.iloc[i]["Option Type"]
            # hedge_entry_datetime = dt.datetime.combine(entry_date, entry_time)
            # hedge_exit_datetime = dt.datetime.combine(exit_date, exit_time)
    
            hedge_df = await fetch_data(
                index=index_str_for_opt,
                start_date=dt.datetime.strptime(entry_date, "%Y-%m-%d").date(),
                end_date=dt.datetime.strptime(exit_date, "%Y-%m-%d").date(),
                start_time=pd.to_datetime(entry_time).time(),
                end_time=exit_time,
                expiry=dt.datetime.strptime(hedge_expiry, "%Y-%m-%d"),
                strike=hedge_strike,
                asset_class=hedge_opt_type[:1],
            )
            if not isinstance(hedge_df, str) and hedge_df is not None:
                hedge_df = hedge_df.to_pandas()
            else:
                print(hedge_df)
                df.loc[i, "Hedge Entry Price"] = 0
                df.loc[i, "Hedge Exit Price"] = 0
                continue
            # print(hedge_df)
    
            hedge_entry_price = hedge_df.iloc[0]["c"]
            hedge_exit_price = hedge_df.iloc[-1]["c"]
    
            print(hedge_entry_price, hedge_exit_price)
    
            df.loc[i, "Hedge Entry Price"] = hedge_entry_price
            df.loc[i, "Hedge Exit Price"] = hedge_exit_price
    
    return df

In [9]:
tb_with_hedge = await add_hedges(tb)
# tb_with_hedge.tail()

2019-01-01
2019-01-01
2019-01-02
2019-01-02
2019-01-03
2019-01-03
2019-01-04
2019-01-04
2019-01-07
2019-01-07
2019-01-08
2019-01-08
2019-01-09
2019-01-09
2019-01-10
2019-01-10
2019-01-11
2019-01-11
2019-01-14
2019-01-14
2019-01-15
2019-01-15
2019-01-16
2019-01-16
2019-01-17
2019-01-17
2019-01-18
2019-01-18
2019-01-21
2019-01-21
2019-01-22
2019-01-22
2019-01-23
2019-01-23
2019-01-24
2019-01-24
2019-01-25
2019-01-25
6.2 11.35
2019-01-28
1.45 2.2
2019-01-28
1.0 2.5
2019-01-29
2.65 2.0
2019-01-29
3.0 0.65
2019-01-30
1.95 0.75
2019-01-30
2.4 3.05
2019-01-31
0.1 0.1
2019-01-31
0.2 0.05
2019-02-01
2019-02-01
2019-02-04
2019-02-04
2019-02-05
2019-02-05
2019-02-06
2019-02-06
2019-02-07
2019-02-07
2019-02-08
2019-02-08
2019-02-11
1.5 1.0
2019-02-11
2.1 1.8
2019-02-12
0.95 0.8
2019-02-12
1.25 1.55
2019-02-13
0.65 0.35
2019-02-13
0.8 0.95
2019-02-14
0.05 0.05
2019-02-14
0.2 0.05
2019-02-15
2.4 2.25
2019-02-15
2.65 6.6
2019-02-18
1.0 1.1
2019-02-18
2.25 7.25
2019-02-19
1.15 1.1
2019-02-19
2.9 5.0
2

In [10]:
tb_with_hedge['Hedge Points'] = tb_with_hedge['Hedge Exit Price'] - tb_with_hedge['Hedge Entry Price']
tb_with_hedge['Hedge PnL'] = tb_with_hedge['Hedge Points'] * tb_with_hedge['Qty']
tb_with_hedge['Hedge ROI%'] = tb_with_hedge.apply(
    lambda row: (row['Hedge PnL'] * 100 / 1000000) if not pd.isna(row['Hedge Points']) else 0,
    axis=1
)
tb_with_hedge['Total ROI%'] = tb_with_hedge['ROI%'] + tb_with_hedge['Hedge ROI%']

In [11]:
tb_with_hedge['ROI%'].sum(), tb_with_hedge['Total ROI%'].sum()

(485.02517979874494, 400.5468390452212)

In [12]:
tb_with_hedge.tail(20)

Day      Time  Strike      Expiry  DTE Option Type  Entry Price  \
2956  2024-12-17  09:15:00   24850  2024-12-19    2          CE        62.70   
2957  2024-12-17  09:15:00   24350  2024-12-19    2          PE        64.35   
2958  2024-12-18  09:15:00   24550  2024-12-19    1          CE        45.50   
2959  2024-12-18  09:15:00   24050  2024-12-19    1          PE        29.80   
2960  2024-12-19  09:15:00   24100  2024-12-19    0          CE        32.90   
2961  2024-12-19  09:15:00   23650  2024-12-19    0          PE        33.50   
2962  2024-12-20  09:15:00   24200  2024-12-26    6          CE       108.15   
2963  2024-12-20  09:15:00   23700  2024-12-26    6          PE       111.20   
2964  2024-12-23  09:15:00   24000  2024-12-26    3          CE        78.15   
2965  2024-12-23  09:15:00   23500  2024-12-26    3          PE        63.45   
2966  2024-12-24  09:15:00   24000  2024-12-26    2          CE        21.35   
2967  2024-12-24  09:15:00   23550  2024-12-26    2          PE        21.90   
2968  2024-12-26  09:15:00   24000  2024-12-26    0          CE        14.60   
2969  2024-12-26  09:15:00   23550  2024-12-26    0          PE        11.35   
2970  2024-12-27  09:15:00   24050  2025-01-02    6          CE          NaN   
2971  2024-12-27  09:15:00   23550  2025-01-02    6          PE          NaN   
2972  2024-12-30  09:15:00   24050  2025-01-02    3          CE          NaN   
2973  2024-12-30  09:15:00   23550  2025-01-02    3          PE          NaN   
2974  2024-12-31  09:15:00   23800  2025-01-02    2          CE          NaN   
2975  2024-12-31  09:15:00   23300  2025-01-02    2          PE          NaN   

      Initial SL  Exit Price            Exit Time  Max Price After Entry  \
2956      94.050      16.300  2024-12-17 15:30:00                  79.15   
2957      96.525      96.525  2024-12-17 10:20:00                 147.00   
2958      68.250      19.500  2024-12-18 15:30:00                  63.45   
2959      44.700      44.700  2024-12-18 12:37:00                  49.00   
2960      49.350       0.050  2024-12-19 15:30:00                  33.25   
2961      50.250       0.050  2024-12-19 15:29:00                  37.50   
2962     162.225     162.225  2024-12-20 09:40:00                 166.80   
2963     166.800     166.800  2024-12-20 13:48:00                 251.10   
2964     117.225      28.000  2024-12-23 15:30:00                  77.05   
2965      95.175      23.650  2024-12-23 15:30:00                  63.90   
2966      32.025      32.025  2024-12-24 10:17:00                  41.60   
2967      32.850      32.850  2024-12-24 09:32:00                  38.10   
2968      21.900      21.900  2024-12-26 09:17:00                  25.40   
2969      17.025      17.025  2024-12-26 13:34:00                  31.75   
2970         NaN         NaN                  NaN                    NaN   
2971         NaN         NaN                  NaN                    NaN   
2972         NaN         NaN                  NaN                    NaN   
2973         NaN         NaN                  NaN                    NaN   
2974         NaN         NaN                  NaN                    NaN   
2975         NaN         NaN                  NaN                    NaN   

      Min Price After Entry  Points         Qty           Pnl  Slippage  \
2956                  16.30  46.400  637.958533  29601.275917   0.79000   
2957                  56.80 -32.175  621.600622 -20000.000000   1.60875   
2958                  15.35  26.000  814.663951  21181.262729   0.65000   
2959                  13.35 -14.900  831.600832 -12390.852391   0.74500   
2960                   0.05  32.850  829.875519  27261.410788   0.32950   
2961                   0.05  33.450  845.665962  28287.526427   0.33550   
2962                  26.80 -54.075  369.856681 -20000.000000   2.70375   
2963                  69.70 -55.600  359.712230 -20000.000000   2.78000   
2964                  19.10  50.150  511.836212  25668.58605

In [13]:
def generate_stats(tb_expiry, ema_window):
    stats_df8 = pd.DataFrame(
        index=range(2019, 2025),
        columns=[
            "Total ROI",
            "Total Trades",
            "Win Rate",
            "Avg Profit% per Trade",
            "Avg Loss% per Trade",
            "Max Drawdown",
            "ROI/DD Ratio",
            "Variation",
        ],
    )
    combined_df_sorted = tb_expiry
    # combined_df_sorted = tb_expiry_ce
    # combined_df_sorted = tb_expiry_pe

    # Iterate over each year
    for year in range(2019, 2025):
        # Filter trades for the current year
        year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]

        # Calculate total ROI
        total_roi = year_trades["Total ROI%"].sum()

        # Calculate total number of trades
        total_trades = len(year_trades)

        # Calculate win rate
        win_rate = (year_trades["Total ROI%"] > 0).mean() * 100

        # Calculate average profit per trade
        avg_profit = year_trades[year_trades["Total ROI%"] > 0]["Total ROI%"].mean()

        # Calculate average loss per trade
        avg_loss = year_trades[year_trades["Total ROI%"] < 0]["Total ROI%"].mean()

        # Calculate maximum drawdown
        max_drawdown = (
            year_trades["Total ROI%"].cumsum() - year_trades["Total ROI%"].cumsum().cummax()
        ).min()

        # Calculate ROI/DD ratio
        roi_dd_ratio = total_roi / abs(max_drawdown)

        variation = f"{ema_window}"

        # Store the statistics in the DataFrame
        stats_df8.loc[year] = [
            total_roi,
            total_trades,
            win_rate,
            avg_profit,
            avg_loss,
            max_drawdown,
            roi_dd_ratio,
            variation,
        ]

    # Calculate overall statistics
    overall_total_roi = stats_df8["Total ROI"].sum()
    overall_total_trades = stats_df8["Total Trades"].sum()
    overall_win_rate = (combined_df_sorted["Total ROI%"] > 0).mean() * 100
    overall_avg_profit = combined_df_sorted[combined_df_sorted["Total ROI%"] > 0][
        "Total ROI%"
    ].mean()
    overall_avg_loss = combined_df_sorted[combined_df_sorted["Total ROI%"] < 0]["Total ROI%"].mean()
    overall_max_drawdown = (
        combined_df_sorted["Total ROI%"].cumsum()
        - combined_df_sorted["Total ROI%"].cumsum().cummax()
    ).min()
    overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)
    overall_variation = variation

    # Store the overall statistics in the DataFrame
    stats_df8.loc["Overall"] = [
        overall_total_roi,
        overall_total_trades,
        overall_win_rate,
        overall_avg_profit,
        overall_avg_loss,
        overall_max_drawdown,
        overall_roi_dd_ratio,
        overall_variation,
    ]
    return {overall_roi_dd_ratio: stats_df8}

In [14]:
tradebook = tb
tradebook["Day"] = pd.to_datetime(tradebook["Day"])
tradebook["Trade Year"] = tradebook["Day"].dt.year

In [15]:
stats = generate_stats(tb_with_hedge, 'Lobster W Hedges')
for x, y in stats.items():
    z = pd.DataFrame(y)
    break

z

Total ROI Total Trades   Win Rate Avg Profit% per Trade  \
2019      76.568229          490  47.346939              1.359464   
2020      72.726552          504  51.587302              1.639153   
2021      89.021069          496  55.846774              1.381284   
2022      78.667025          496  55.241935              1.476727   
2023       42.16773          492  54.674797              0.903622   
2024      41.396233          498  48.192771              1.370851   
Overall  400.546839         2976  52.150538              1.353668   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio         Variation  
2019              -1.159357   -13.565734     5.644238  Lobster W Hedges  
2020              -1.472721   -13.042872     5.575961  Lobster W Hedges  
2021              -1.365557   -10.514674     8.466365  Lobster W Hedges  
2022              -1.481619    -9.034319     8.707577  Lobster W Hedges  
2023              -0.952164    -7.962743     5.295629  Lobster W Hedges  
2024              -1.229094   -13.121953     3.154731  Lobster W Hedges  
Overall           -1.282312   -13.565734    29.526367  Lobster W Hedges

In [16]:
# import pandas as pd

# df = pd.DataFrame(tb_with_hedge)

# cols = df.columns.tolist()

# # Move 'Cumulative ROI%', 'Max Cumulative ROI%' and 'DD' to the last
# desired_cols = ['Cumulative ROI%', 'Max Cumulative ROI%', 'DD']
# cols = [col for col in cols if col not in desired_cols] + desired_cols
# # Reassign the columns to the DataFrame
# df = df[cols]

# df


In [17]:
tb = tb_with_hedge
tb['Cumulative ROI%'] = tb['Total ROI%'].cumsum()
tb['Max Cumulative ROI%'] = tb['Cumulative ROI%'].cummax()  # Maximum value so far
tb['DD'] = tb['Cumulative ROI%'] - tb['Max Cumulative ROI%']  # Drawdown
tb

Day      Time  Strike      Expiry  DTE Option Type  Entry Price  \
0    2019-01-01  09:15:00   11000  2019-01-03    2          CE          NaN   
1    2019-01-01  09:15:00   10750  2019-01-03    2          PE          NaN   
2    2019-01-02  09:15:00   11000  2019-01-03    1          CE          NaN   
3    2019-01-02  09:15:00   10750  2019-01-03    1          PE          NaN   
4    2019-01-03  09:15:00   10900  2019-01-03    0          CE          NaN   
5    2019-01-03  09:15:00   10700  2019-01-03    0          PE          NaN   
6    2019-01-04  09:15:00   10800  2019-01-10    6          CE          NaN   
7    2019-01-04  09:15:00   10600  2019-01-10    6          PE          NaN   
8    2019-01-07  09:15:00   10900  2019-01-10    3          CE          NaN   
9    2019-01-07  09:15:00   10700  2019-01-10    3          PE          NaN   
10   2019-01-08  09:15:00   10900  2019-01-10    2          CE          NaN   
11   2019-01-08  09:15:00   10700  2019-01-10    2          PE          NaN   
12   2019-01-09  09:15:00   10950  2019-01-10    1          CE          NaN   
13   2019-01-09  09:15:00   10750  2019-01-10    1          PE          NaN   
14   2019-01-10  09:15:00   10950  2019-01-10    0          CE          NaN   
15   2019-01-10  09:15:00   10750  2019-01-10    0          PE          NaN   
16   2019-01-11  09:15:00   10950  2019-01-17    6          CE          NaN   
17   2019-01-11  09:15:00   10750  2019-01-17    6          PE          NaN   
18   2019-01-14  09:15:00   10900  2019-01-17    3          CE          NaN   
19   2019-01-14  09:15:00   10700  2019-01-17    3          PE          NaN   
20   2019-01-15  09:15:00   10900  2019-01-17    2          CE          NaN   
21   2019-01-15  09:15:00   10650  2019-01-17    2          PE          NaN   
22   2019-01-16  09:15:00   11000  2019-01-17    1          CE          NaN   
23   2019-01-16  09:15:00   10800  2019-01-17    1          PE          NaN   
24   2019-01-17  09:15:00   11050  2019-01-17    0          CE          NaN   
25   2019-01-17  09:15:00   10800  2019-01-17    0          PE          NaN   
26   2019-01-18  09:15:00   11000  2019-01-24    6          CE          NaN   
27   2019-01-18  09:15:00   10800  2019-01-24    6          PE          NaN   
28   2019-01-21  09:15:00   11050  2019-01-24    3          CE          NaN   
29   2019-01-21  09:15:00   10800  2019-01-24    3          PE          NaN   
30   2019-01-22  09:15:00   11050  2019-01-24    2          CE          NaN   
31   2019-01-22  09:15:00   10850  2019-01-24    2          PE          NaN   
32   2019-01-23  09:15:00   11050  2019-01-24    1          CE          NaN   
33   2019-01-23  09:15:00   10800  2019-01-24    1          PE          NaN   
34   2019-01-24  09:15:00   10950  2019-01-24    0          CE          NaN   
35   2019-01-24  09:15:00   10750  2019-01-24    0          PE          NaN   
36   2019-01-25  09:15:00   10950  2019-01-31    6          CE        66.45   
37   2019-01-25  09:15:00   10750  2019-01-31    6          PE        25.30   
38   2019-01-28  09:15:00   10900  2019-01-31    3          CE        32.40   
39   2019-01-28  09:15:00   10700  2019-01-31    3          PE        50.00   
40   2019-01-29  09:15:00   10750  2019-01-31    2          CE        31.30   
41   2019-01-29  09:15:00   10550  2019-01-31    2          PE        38.20   
42   2019-01-30  09:15:00   10800  2019-01-31    1          CE        16.65   
43   2019-01-30  09:15:00   10600  2019-01-31    1          PE        16.05   
44   2019-01-31  09:15:00   10800  2019-01-31    0          CE         2.60   
45   2019-01-31  09:15:00   10600  2019-01-31    0          PE         3.80   
46   2019-02-01  09:15:00   10950  2019-02-07    6          CE          NaN   
47   2019-02-01  09:15:00   10750  2019-02-07    6          PE          NaN   
48   2019-02-04  09:15:00   11000  2019-02-07    3          CE          NaN   
49   2019-02-04  09:15:00   10750  2019-02-07    3          PE

In [60]:
# tb = tb.drop(columns=['RSI on Entry', 'day'])

In [25]:
tb_with_hedge.to_csv('Budget-OpSell-RB.csv', index=False)

In [84]:
import pandas as pd

def calculate_dte_stats(df):
    """
    Calculate stats grouped by DTE: 
    - Returns Sum for each DTE
    - Max Drawdown (DD) for each DTE
    - Ratio of Returns Sum to Max DD for each DTE

    Parameters:
        df (pd.DataFrame): DataFrame containing a 'DTE' column, 'returns', and 'drawdown' columns.
    
    Returns:
        pd.DataFrame: DataFrame with aggregated statistics by DTE.
    """
    # print(df.columns)
    if 'DTE' not in df.columns or 'Total ROI%' not in df.columns or 'DD' not in df.columns:
        raise ValueError("DataFrame must contain 'DTE', 'returns', and 'drawdown' columns.")
    
    # Group by DTE and calculate required stats
    grouped_stats = df.groupby('DTE').agg(
        returns_sum=('Total ROI%', 'sum'),
        max_drawdown=('DD', 'min'),  # Assuming 'drawdown' contains negative values
        total_trades=('DTE', 'count')
    ).reset_index()
    
    # Calculate ratio of returns sum to max drawdown
    grouped_stats['returns_to_max_dd_ratio'] = (
        grouped_stats['returns_sum'] / grouped_stats['max_drawdown'].abs()
    )

    return grouped_stats


In [87]:
stats_dte = calculate_dte_stats(tb)
stats_dte[1:]

DTE  returns_sum  max_drawdown  total_trades  returns_to_max_dd_ratio
1    0   216.077355    -12.095041           622                17.864955
2    1   158.556458    -12.541781           590                12.642260
3    2   111.501167    -13.086746           594                 8.520160
4    3   101.348922    -14.555113           566                 6.963115
5    4     0.000000           NaN             4                      NaN
6    5     3.834230    -12.491741            32                 0.306941
7    6   129.145841    -13.698995           566                 9.427395